In [1]:
import sqlite3
import pandas as pd

import pystac_client
import odc.stac

In [2]:
# Connecting to sqlite 
conn = sqlite3.connect('fire.db')

# Create a cursor object
cursor = conn.cursor()

In [3]:
# set this to True if you run it the first time, to create the database
first = False

if first == True:
    # Read CSV file into a pandas DataFrame
    df = pd.read_csv('./Data/base_data_1986-2018.csv')

    df.drop('time', axis=1, inplace=True)
    df.drop('index_right', axis=1, inplace=True)
    df.month = pd.to_datetime(df.month, format='%Y-%m')

    # Write the DataFrame to the SQLite database
    df.to_sql('ground_data', conn, if_exists='replace', index=False)

    # Commit the changes
    conn.commit()

In [4]:
cursor.execute('''SELECT * from ground_data LIMIT 10''')
cursor.fetchall()

[('1986-01-01 00:00:00',
  -39.05,
  146.34,
  'POINT (146.34 -39.05)',
  584.91650390625,
  5.71484375,
  288.8251953125,
  72.26092529296875,
  2.046238660812378,
  -0.4,
  0.82,
  0.0,
  0.0,
  5831.0),
 ('1986-01-01 00:00:00',
  -38.94,
  146.34,
  'POINT (146.34 -38.94)',
  639.8798828125,
  5.048828125,
  289.13623046875,
  71.379150390625,
  2.046238660812378,
  -0.4,
  0.82,
  0.0,
  1.0,
  5832.0),
 ('1986-01-01 00:00:00',
  -38.94,
  146.45,
  'POINT (146.45 -38.94)',
  640.3271484375,
  5.49609375,
  289.040771484375,
  72.02374267578125,
  2.046238660812378,
  -0.4,
  0.82,
  0.0,
  1.0,
  5942.0),
 ('1986-01-01 00:00:00',
  -38.83,
  145.9,
  'POINT (145.9 -38.83)',
  890.787109375,
  5.88671875,
  289.68359375,
  69.36932373046875,
  -0.2895850241184234,
  -0.4,
  0.82,
  0.0,
  0.0,
  5393.0),
 ('1986-01-01 00:00:00',
  -38.83,
  146.01,
  'POINT (146.01 -38.83)',
  875.54052734375,
  5.626953125,
  289.466064453125,
  70.56951904296875,
  -0.2895850241184234,
  -0.4,
  

In [5]:
#Get all tables
def get_all_tables(cursor):
    sql_query = """SELECT name FROM sqlite_master  
      WHERE type='table';"""
    cursor.execute(sql_query)
    return cursor.fetchall()

# Get column names and data types for each table
def get_table_info(cursor, table_name):
    cursor.execute(f'PRAGMA table_info({table_name})')
    return cursor.fetchall()

In [6]:
tables = [table[0] for table in get_all_tables(cursor)]

for table in tables:
    print(f"Table: {table}")
    for column in get_table_info(cursor, table):
        print(f"Column: {column[1]}, Type: {column[2]}")
    print("\n")

Table: ground_data
Column: month, Type: TIMESTAMP
Column: lat, Type: REAL
Column: lon, Type: REAL
Column: geometry, Type: TEXT
Column: mrso, Type: REAL
Column: sfcWind, Type: REAL
Column: tas, Type: REAL
Column: hurs, Type: REAL
Column: pdsi, Type: REAL
Column: MEI, Type: REAL
Column: SOI, Type: REAL
Column: bushfire_count, Type: REAL
Column: prescribed_count, Type: REAL
Column: grid_id, Type: REAL




In [7]:
catalog = pystac_client.Client.open("https://explorer.dea.ga.gov.au/stac")

In [8]:
odc.stac.configure_rio(
    cloud_defaults=True,
    aws={"aws_unsigned": True},
)

In [9]:
def get_month_lat_long(cursor):
    sql_query = '''SELECT strftime('%Y-%m', month) as month, lat, lon, grid_id from ground_data'''
    cursor.execute(sql_query)
    return cursor.fetchall()

def create_stac_data_table(cursor, conn):
    # Create a new table with the required columns
    cursor.execute('''
    CREATE TABLE IF NOT EXISTS stac_data (
        time TEXT,
        y REAL,
        x REAL,
        grid_id REAL,
        bs_pc_10 REAL,
        bs_pc_50 REAL,
        bs_pc_90 REAL,
        pv_pc_10 REAL,
        pv_pc_50 REAL,
        pv_pc_90 REAL,
        npv_pc_10 REAL,
        npv_pc_50 REAL,
        npv_pc_90 REAL
    )
    ''')

    # Commit the changes
    conn.commit()

def write_stac_data_to_db(cursor, conn, data):
    for item in data:
        cursor.execute('''
        INSERT INTO stac_data (time, y, x, grid_id, bs_pc_10, bs_pc_50, bs_pc_90, pv_pc_10, pv_pc_50, pv_pc_90, npv_pc_10, npv_pc_50, npv_pc_90)
        VALUES (?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?)
        ''', (
            item['time'], item['y'], item['x'], item['grid_id'],
            item['bs_pc_10'], item['bs_pc_50'], item['bs_pc_90'],
            item['pv_pc_10'], item['pv_pc_50'], item['pv_pc_90'],
            item['npv_pc_10'], item['npv_pc_50'], item['npv_pc_90']
        ))

    # Commit the changes
    conn.commit()

In [ ]:
#create_stac_data_table(cursor, conn)

In [ ]:
data_tiles = get_month_lat_long(cursor)

print(len(data_tiles))

for data in data_tiles:

    bbox = [data[2] - 0.05, data[1] - 0.05, data[2] + 0.05, data[1] + 0.05]

    start_date = f"{data[0][:4]-1}-12-31"
    end_date = f"{data[0][:4]+1}-01-01"

    print(f"Searching for data in {start_date} to {end_date} for lat: {data[1]} and long: {data[2]}")

    # Set product ID as the STAC "collection"
    collections = ["ga_ls_fc_pc_cyear_3"]

    # Build a query with the parameters above
    query = catalog.search(
        bbox=bbox,
        collections=collections,
        datetime=f"{start_date}/{end_date}",
    )

    if len(list(query.items())) == 0:
        print("No data found")
        continue

    # Search the STAC catalog for all items matching the query
    items = list(query.items())
    print(f"Found: {len(items):d} datasets")

    # Load the data using the odc.stac module
    ds = odc.stac.load(
                items=items,
                crs="EPSG:3577",
                lat=(bbox[1], bbox[3]),
                lon=(bbox[0], bbox[2]),
                time=(start_date, end_date))
    
    data_entry = {
        'time': str(ds.time.values[0]),
        'y': float(ds.y.values[0]),
        'x': float(ds.x.values[0]),
        'grid_id': data[3],
        'bs_pc_10': float(ds.bs_pc_10.mean().values),
        'bs_pc_50': float(ds.bs_pc_50.mean().values),
        'bs_pc_90': float(ds.bs_pc_90.mean().values),
        'pv_pc_10': float(ds.pv_pc_10.mean().values),
        'pv_pc_50': float(ds.pv_pc_50.mean().values),
        'pv_pc_90': float(ds.pv_pc_90.mean().values),
        'npv_pc_10': float(ds.npv_pc_10.mean().values),
        'npv_pc_50': float(ds.npv_pc_50.mean().values),
        'npv_pc_90': float(ds.npv_pc_90.mean().values)
    }

    write_stac_data_to_db(cursor, conn, [data_entry])


294126
Searching for data in 1986-01-01 to 1986-12-31 for lat: -39.05 and long: 146.34
No data found
Searching for data in 1986-01-01 to 1986-12-31 for lat: -38.94 and long: 146.34
No data found
Searching for data in 1986-01-01 to 1986-12-31 for lat: -38.94 and long: 146.45
No data found
Searching for data in 1986-01-01 to 1986-12-31 for lat: -38.83 and long: 145.9
No data found
Searching for data in 1986-01-01 to 1986-12-31 for lat: -38.83 and long: 146.01
No data found
Searching for data in 1986-01-01 to 1986-12-31 for lat: -38.83 and long: 146.23
No data found
Searching for data in 1986-01-01 to 1986-12-31 for lat: -38.72 and long: 143.26
No data found
Searching for data in 1986-01-01 to 1986-12-31 for lat: -38.72 and long: 143.37
No data found
Searching for data in 1986-01-01 to 1986-12-31 for lat: -38.72 and long: 143.48
No data found
Searching for data in 1986-01-01 to 1986-12-31 for lat: -38.72 and long: 143.59
No data found
Searching for data in 1986-01-01 to 1986-12-31 for lat

APIError: <html>
<head><title>502 Bad Gateway</title></head>
<body>
<center><h1>502 Bad Gateway</h1></center>
</body>
</html>
